# Language Modeling with Keras

In [39]:
import itertools
import numpy as np
import string
from keras.layers import Input, Embedding, merge, Flatten, Reshape, Lambda, LSTM
import keras.backend as K
from keras.models import Model

In [33]:

#imports a massive dataset of sentences found on wikipedia
with open('training_data.txt') as f:
    content = f.readlines()

# you may also want to remove whitespace characters like `\n` at the end of each line,
# also strips the punctuation
sentences = [x.strip().translate(None, string.punctuation) for x in content] 

lemma = lambda x: x.strip().lower().split(' ')
sentences_lemmatized = [lemma(sentence) for sentence in sentences]
words = set(itertools.chain(*sentences_lemmatized))
# set(['boy', 'fed', 'ate', 'cat', 'kicked', 'hat'])

# dictionaries for converting words to integers and vice versa
word2idx = dict((v, i) for i, v in enumerate(words))
idx2word = list(words)

# convert the sentences a numpy array
to_idx = lambda x: [word2idx[word] for word in x]
sentences_idx = [to_idx(sentence) for sentence in sentences_lemmatized]
# Sets the maximum word length of each sentence
max_len = 100
# If the sentence is too long, good by
for i in range(len(sentences_idx)-1, -1, -1):
    if len(sentences_idx[i]) > max_len:
        print i
        sentences_idx.pop(i)
    elif len(sentences_idx[i]) < max_len:
        sentences_idx[i] = [0] * (max_len - len(sentences_idx[i])) + sentences_idx[i]
sentences_array = np.asarray(sentences_idx, dtype='int32')
#TODO find a way to set all sentence lengths to be the same

1748


In [34]:
print len(sentences_idx)
print len(word2idx)

3148
3727


In [42]:
n_words = len(words)
n_embed_dims = 150

# put together a model to predict
input_sentence = Input(shape=(max_len,), dtype='int32')
input_embedding = Embedding(n_words, n_embed_dims)(input_sentence)
output = LSTM(100)(input_embedding)

predict_boy = Model(input=[input_sentence], output=[output])
predict_boy.compile(optimizer='rmsprop', loss='mse')

# fit the model to predict what color each person is
predict_boy.fit([sentences_array[:len(sentences_array)-1]], [sentences_array[1:]], epochs=20, verbose=3)
embeddings = predict_boy.layers[1].get_weights()

# print out the embedding vector associated with each word
for i in range(n_words):
    print('{}: {}'.format(idx2word[i], embeddings[0][i]))

/Users/TomCat/python-neural-nets/venv/lib/python2.7/site-packages/ipykernel_launcher.py:9: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=[<tf.Tenso..., inputs=[<tf.Tenso...)`
  if __name__ == '__main__':


Epoch 1/20
Epoch 2/20
Epoch 3/20
Epoch 4/20
Epoch 5/20
Epoch 6/20
Epoch 7/20
Epoch 8/20
Epoch 9/20
Epoch 10/20
Epoch 11/20
Epoch 12/20
Epoch 13/20
Epoch 14/20
Epoch 15/20
Epoch 16/20
Epoch 17/20
Epoch 18/20
Epoch 19/20
Epoch 20/20
: [ -3.31486724e-02  -2.60154326e-02   3.79784629e-02  -7.80165847e-03
  -8.77078474e-02   8.61603022e-02   4.66532446e-02   8.68642405e-02
   5.76889217e-02   2.50420645e-02   7.83553347e-02  -1.26796529e-01
   1.37907425e-02   9.28878598e-03   7.42345117e-03   8.70465394e-03
  -1.01775713e-01  -1.29781626e-02  -3.92830521e-02  -7.36117736e-03
  -3.18551250e-02   8.18228200e-02   1.31253123e-01   1.04070371e-02
  -9.04851481e-02   2.87538432e-02  -3.53362877e-03   4.72733080e-02
   4.80951257e-02   5.55666760e-02  -3.95693108e-02   1.50584439e-02
  -1.31993294e-01   1.33971527e-01   8.39162804e-03   2.10994985e-02
  -5.68298250e-03  -5.31782070e-03   8.48728344e-02   6.25302270e-02
   1.03624634e-01   7.35854357e-02  -4.86082397e-02   1.13978737e-03
   1.706

tired: [-0.01670814 -0.0296971  -0.04536513  0.03821233  0.07856542 -0.08124384
 -0.07317739  0.00200022 -0.04269777 -0.07507965  0.03807797  0.05083895
 -0.08189417  0.01952591 -0.00443604 -0.06913395 -0.05025536  0.00892512
 -0.08007706 -0.00887005  0.00508684  0.0760471  -0.01611882 -0.04790571
  0.06430583  0.02127451  0.03152511  0.04629466 -0.06581204  0.06398878
 -0.01767869  0.01477208 -0.11909132  0.07372864  0.02332636 -0.0505269
  0.01177562 -0.00065852  0.05565528  0.06568798 -0.05903695 -0.03721549
  0.08021691 -0.07996593 -0.07865418 -0.05277403 -0.05133933 -0.08342865
  0.07128657 -0.02401817  0.05961581 -0.12576763  0.13042785 -0.05034737
 -0.06910268 -0.07458729 -0.02073638  0.0097468  -0.04360864  0.06146155
  0.12286989 -0.06450839  0.02516756  0.0473565   0.06055964 -0.01093467
 -0.06415048  0.07889876 -0.02944817  0.04922621 -0.06532588 -0.09600638
 -0.00704818  0.00636963 -0.06656518 -0.05029281  0.11599903 -0.03787442
 -0.02231437 -0.01423651 -0.02935203  0.00363

  -1.01895824e-01   2.32172862e-01]
stared: [ 0.08312599  0.00048518 -0.04150026  0.04086363 -0.05759315 -0.04533793
 -0.00263166  0.03430782 -0.02095158 -0.00111037  0.07434657 -0.01502183
 -0.07466488  0.02373674  0.08358943 -0.06135694 -0.10904308  0.04971961
 -0.0202133  -0.10755318 -0.01148137  0.07875113 -0.01013717 -0.00152267
  0.05637672  0.01778953  0.03864509  0.01193738 -0.08352061  0.07970622
  0.02604533  0.04413311 -0.02131317  0.01412319 -0.02686282  0.00212809
  0.0576162   0.0350398   0.03341071  0.04063284  0.00687958  0.03718444
  0.02179405  0.01580655 -0.08163754 -0.02517751 -0.01748735 -0.00194343
  0.05313476 -0.06372628 -0.0561398  -0.0346789   0.04431954 -0.06830826
 -0.01029619 -0.09572686 -0.03297378  0.05587396 -0.03307361  0.03632559
  0.0946843  -0.01233135 -0.07789137 -0.05429439  0.09903941  0.06430676
 -0.06992798 -0.05019164  0.06942513  0.0638206  -0.07058129 -0.04114456
  0.01801225 -0.09823341 -0.04867656 -0.0752231  -0.02584584  0.02890632
  0.021

  -4.51148748e-02   3.10017746e-02]
swings: [ 0.09243585 -0.1215717  -0.05987607  0.14466803 -0.08108143 -0.1458804
 -0.14122097  0.08602378 -0.08071846 -0.06632002  0.06013913  0.10365687
 -0.09448812  0.14345598  0.14634424 -0.13431861 -0.08260872  0.10622495
 -0.1363512  -0.09466403 -0.09767558  0.09155899  0.08625492 -0.15102108
  0.15655331  0.11013599  0.12968972  0.09037444 -0.15253744  0.10793421
  0.1647784   0.14064284 -0.11690966  0.09775235 -0.06528372 -0.01871086
  0.11322317  0.05760138  0.11149356 -0.02871479  0.04844469  0.09669458
  0.14024594 -0.13251121 -0.15963981 -0.15225926 -0.08342472 -0.12094447
  0.13914908 -0.09294265 -0.125635   -0.11655127  0.09920896 -0.1252656
 -0.07965537 -0.09282794 -0.12678958  0.07122285 -0.18362927  0.13388182
  0.14027558  0.10419537 -0.10252336 -0.13978253  0.09815546  0.10009882
 -0.13876821 -0.11899643 -0.02598009  0.09084819 -0.13876756 -0.08999068
  0.11844432 -0.13678369 -0.07980871 -0.1454608   0.08500267 -0.0427372
  0.119023

...

  0.11038481  0.04800065  0.16137528  0.12475902  0.05213515  0.05350177]
swinging: [ 0.06436843 -0.01840422 -0.03251437  0.05139428 -0.03606818 -0.07256345
 -0.03366743  0.09575772 -0.00472193  0.01084811  0.00826177  0.06417699
 -0.0865332   0.04347968  0.04301421 -0.00636506 -0.0732986   0.02780843
 -0.04267799 -0.07944069  0.01349111  0.02004591 -0.02620981 -0.02476567
  0.03298161  0.08877842  0.01218721  0.00894527 -0.0438305   0.0028735
  0.04385912  0.00891208 -0.03353909  0.04292801 -0.0102336  -0.04420799
  0.04518482  0.03319113  0.00838805 -0.02121019  0.03933488  0.04510176
  0.0434853  -0.03010201 -0.02607388 -0.05150505 -0.08637951 -0.04369544
  0.07923332  0.0032458  -0.05649841 -0.02481092  0.0189306  -0.09013653
 -0.03654846 -0.07710893  0.00365992  0.01508616 -0.09280688  0.00534571
  0.04257796  0.07294597 -0.10481076 -0.07573976  0.02026748  0.07769646
 -0.0414524  -0.00446412  0.02517723  0.02363799 -0.01541539 -0.080216
 -0.01673506 -0.0005805  -0.00603558 -0.014

wed: [ 0.1748068  -0.24008386 -0.19874395  0.19245635 -0.15068863 -0.26652876
 -0.19511087  0.18135987 -0.11108499 -0.11709844  0.16226164  0.06736577
 -0.18467771  0.23608145  0.16098312 -0.19177881 -0.21994668  0.15178332
 -0.19997701 -0.260979   -0.1288048   0.19986473  0.08973007 -0.25612417
  0.15140167  0.23438391  0.15751679  0.21474536 -0.20797597  0.2106811
  0.16914979  0.20673706 -0.1588425   0.1885889  -0.02013249 -0.06352001
  0.18406886  0.16778773  0.21131028 -0.05343059  0.05841325  0.13094878
  0.1973272  -0.27241254 -0.17627262 -0.11967579 -0.25823468 -0.11443315
  0.22053388 -0.1676338  -0.1775562  -0.20426106  0.11684331 -0.24398035
 -0.19586861 -0.1646537  -0.13829783  0.13106318 -0.18462427  0.17442261
  0.21360298  0.12766558 -0.14800145 -0.23504156  0.21110646  0.23561463
 -0.11593562 -0.18580951 -0.02532978  0.20451236 -0.23603755 -0.2846522
  0.05024763 -0.14751022 -0.20737395 -0.10499571  0.03400553 -0.15087827
  0.15411304 -0.23681921 -0.1280382   0.23882774

hair: [ 0.24317603 -0.2606993  -0.22790316  0.1816158  -0.15183145 -0.16653275
 -0.19141319  0.18946023 -0.20181037 -0.18563624  0.23565495  0.17228107
 -0.17765723  0.21001287  0.19025108 -0.22194776 -0.23450236  0.22060646
 -0.23234992 -0.2714026  -0.23248333  0.18565048  0.17531252 -0.26051822
  0.20893873  0.20012128  0.18233763  0.28699756 -0.18299969  0.24178711
  0.24700722  0.22644021 -0.17104815  0.1884592  -0.17722119  0.14391552
  0.21647736  0.18466932  0.30802089 -0.12103147  0.1291323   0.21840112
  0.19281846 -0.23550339 -0.22948416 -0.15807095 -0.22769684 -0.18288758
  0.30210388 -0.21697178 -0.14475819 -0.26380575  0.15555231 -0.25090903
 -0.17432462 -0.27357498 -0.19912674  0.1624047  -0.23724301  0.15479332
  0.20526579  0.15243721 -0.25049165 -0.24661653  0.23101015  0.23435593
 -0.16302903 -0.17397568 -0.17593431  0.22655247 -0.16770613 -0.27648526
  0.11504988 -0.21073297 -0.18234979 -0.2000009   0.1053526  -0.13751176
  0.20951088 -0.18934202 -0.23269695  0.17205

promise: [ 0.11215653 -0.18866105 -0.14001887  0.16633731 -0.11014756 -0.08804511
 -0.12292919  0.14584868 -0.02504265 -0.09090228  0.105179    0.04638407
 -0.19322461  0.10717675  0.11421548 -0.18926553 -0.10824595  0.14313737
 -0.1952424  -0.18682742 -0.11301652  0.13165751  0.06428447 -0.10885307
  0.1967888   0.20387883  0.13684149  0.13714264 -0.08333746  0.17475885
  0.10545987  0.11685727 -0.15010908  0.18211998 -0.06699266 -0.1045437
  0.16167514  0.13919759  0.1293629   0.00339414  0.09348655  0.11639628
  0.12367666 -0.12860526 -0.20971511 -0.16963698 -0.19058238 -0.07660042
  0.15730043 -0.09213594 -0.10677822 -0.13727579  0.08056302 -0.13141277
 -0.12276267 -0.15048893 -0.0719993   0.09878284 -0.15607308  0.09851018
  0.21949993  0.04752239 -0.16283712 -0.10303861  0.18545927  0.19338128
 -0.10551081 -0.08063554  0.02768249  0.18713145 -0.10819071 -0.15788063
  0.09277434 -0.16849996 -0.1486544  -0.13277417  0.02763893 -0.11479446
  0.13460425 -0.17827645 -0.18620554  0.197

eat: [ 0.2477562  -0.27905241 -0.23883507  0.29868183 -0.28156292 -0.25826707
 -0.27288109  0.19116323 -0.24282242 -0.24426842  0.29372111  0.24059924
 -0.3136386   0.22659595  0.2167166  -0.26585624 -0.21199819  0.29347965
 -0.30589053 -0.17489067 -0.25710189  0.3345075   0.17847796 -0.24542123
  0.2504676   0.26897556  0.20849495  0.27140924 -0.24812692  0.29628325
  0.29840782  0.27254087 -0.31753314  0.25724173 -0.14978856  0.20771071
  0.22811289  0.30750197  0.35003942 -0.14149831  0.21208222  0.26688814
  0.28877634 -0.31620419 -0.29107901 -0.25268465 -0.22672233 -0.24689484
  0.28423151 -0.2967259  -0.23767813 -0.27025595  0.29504457 -0.29468194
 -0.22745825 -0.31410864 -0.26966462  0.23234846 -0.21999337  0.18483025
  0.31741405  0.22027771 -0.20172438 -0.29579461  0.2385143   0.26844177
 -0.27271125 -0.25680169 -0.19896898  0.25683954 -0.25173324 -0.28926417
  0.22059147 -0.26609212 -0.25302839 -0.25339559  0.12544483 -0.25747591
  0.27858499 -0.26970163 -0.28845623  0.268225